# Radio Link Failure Prediction Challenge

In [1]:
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras import layers



import pandas as pd
from zipfile import ZipFile
import wget
import py7zr

from sklearn import tree
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import OneHotEncoder
from sklearn import metrics
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

from xgboost import XGBClassifier, plot_importance

from matplotlib import pyplot as plt


Based on template available here: https://github.com/Turkcell/ITU-AIMLin5GChallenge-2021/blob/4938c53979d650f94d5208ff4cb977ea954b6907/RLF_Prediction_ITU_AIML_Challenge_Data/TurkcellExampleProject.ipynb

## Processing the Data

In [2]:
filename = wget.download('https://github.com/Turkcell/ITU-AIMLin5GChallenge-2021/raw/main/RLF_Prediction_ITU_AIML_Challenge_Data/RLF_Prediction_ITU_AIML_Challenge_Data.7z')

  6% [....                                                                    ]  1425408 / 22740563

 18% [.............                                                           ]  4259840 / 22740563

 23% [.................                                                       ]  5373952 / 22740563

 30% [.....................                                                   ]  6930432 / 22740563

 39% [............................                                            ]  8904704 / 22740563

 43% [...............................                                         ]  9936896 / 22740563

 48% [..................................                                      ] 11034624 / 22740563

100% [........................................................................] 22740563 / 22740563

In [3]:
archive = py7zr.SevenZipFile('RLF_Prediction_ITU_AIML_Challenge_Data.7z', mode='r')
archive.extractall()
archive.close()

In [4]:
#Read the Data
data_zip_path = "RLF_Prediction_ITU_AIML_Challenge_Data/RegionA.zip"
# Zip file reading
def read_table_from_zip(zip_path, table_name):
    with ZipFile(zip_path) as zip_file:
        with zip_file.open(table_name) as file:
            df = pd.read_csv(file, sep="\t", index_col=0)
            if "datetime" in df:
                df["datetime"] = pd.to_datetime(df["datetime"])
            return df

In [5]:
#Read rl-kpis
rl_kpis = read_table_from_zip(data_zip_path, "rl-kpis.tsv")
print(f"rl_kpis.shape: {rl_kpis.shape}")
rl_kpis.head()

rl_kpis.shape: (1992986, 18)


type   datetime  tip  mlid mw_connection_no   site_id  card_type  \
0  ENK 2018-12-31  FAR  A0BE        1,349,988  RL_;ABDV  cardtype1   
1  ENK 2018-12-31  FAR  A0BI        1,349,988  RL_;ABDV  cardtype1   
2  ENK 2018-12-31  FAR  A5AB        1,344,018  RL_;ABDV  cardtype4   
3  NEC 2018-12-31  FAR  A8CQ        1,351,204  RL_;ABDV  cardtype5   
4  NEC 2018-12-31  FAR  A8DQ        1,351,204  RL_;ABDV  cardtype5   

  adaptive_modulation freq_band  severaly_error_second  error_second  \
0              Enable        f3                    0.0           0.0   
1              Enable        f3                    0.0           0.0   
2              Enable        f3                    0.0           0.0   
3              Enable        f2                    0.0           0.0   
4              Enable        f2                    0.0           0.0   

   unavail_second  avail_time  bbe  rxlevmax  capacity modulation    rlf  
0             0.0        86.4  0.0     -31.0     456.0    1024QAM  False  
1             0.0        86.4  0.0     -30.7     456.0    1024QAM  False  
2             0.0        86.4  0.0     -34.4     406.0     512QAM  False  
3             0.0        86.4  0.0     -35.3     247.0   2048QAM*  False  
4             0.0        86.4  0.0     -35.3     247.0   2048QAM*  False

In [6]:
#Read rl-sites
rl_sites = read_table_from_zip(data_zip_path, "rl-sites.tsv")
print(f"rl-sites.shape: {rl_sites.shape}")
rl_sites.head()

rl-sites.shape: (1674, 3)


site_id  groundheight clutter_class
0  RL_;ABDV      107.9658     OPEN LAND
1  RL_;ABL>       97.9733     OPEN LAND
2  RL_;ABTP        3.0446     OPEN LAND
3  RL_;AC?E       85.0143     OPEN LAND
4  RL_;ADKP      192.9800    DENSE TREE

In [7]:
#Read distances
distances = read_table_from_zip(data_zip_path, "distances.tsv")
print(f"distances.shape: {distances.shape}")
distances.head()

distances.shape: (1694, 1694)


WS_19111  WS_17047  WS_18397  WS_17062  WS_17813  WS_17064  \
WS_19111   0.00000  18.65248  60.37075  41.38519  44.21637  53.29280   
WS_17047  18.65248   0.00000  73.44414  57.53957  60.28748  69.69699   
WS_18397  60.37075  73.44414   0.00000  23.48214  21.31712  19.65172   
WS_17062  41.38519  57.53957  23.48214   0.00000   2.83118  12.15742   
WS_17813  44.21637  60.28748  21.31712   2.83118   0.00000   9.49278   

          WS_19112  WS_17063  WS_18736  WS_17065  ...  RL_]=UC>  RL_]ITCK  \
WS_19111  57.28976  63.45174  62.78558  54.45858  ...  56.29052  39.88633   
WS_17047  73.02779  79.27304  76.94148  69.61372  ...  72.02855  55.54109   
WS_18397  15.23841  16.82054   6.57833  11.65780  ...  15.07187  22.73271   
WS_17062  15.90457  22.06655  23.23233  13.98936  ...  14.98860   3.49734   
WS_17813  13.07339  19.23537  20.65096  11.24145  ...  12.15742   5.24601   

          RL_[KBDF  RL_X;O@O  RL_b?LMI  RL_]IC?O  RL_S:PQD  RL_JEZWL  \
WS_19111  46.79774  59.53805  42.80078  41.30192  41.46846  47.79698   
WS_17047  63.03539  76.02551  58.87189  56.87341  57.53957  63.78482   
WS_18397  20.48442  20.40115  21.98328  21.65020  22.81598  18.98556   
WS_17062   5.49582  18.40267   1.66540   2.99772   0.91597   6.41179   
WS_17813   2.74791  15.73803   1.41559   3.99696   2.74791   3.58061   

          RL_LKEII  RL_[EOMJ  
WS_19111  52.29356  42.63424  
WS_17047  67.44870  58.62208  
WS_18397  12.82358  21.98328  
WS_17062  11.90761   1.49886  
WS_17813   9.24297   1.66540  

[5 rows x 1694 columns]

In [8]:
#Read met-forecast
met_forecast = read_table_from_zip(data_zip_path, "met-forecast.tsv")
print(f"met-forecast.shape: {met_forecast.shape}")
met_forecast.head()

met-forecast.shape: (20323, 38)


station_no   datetime report_time weather_day1  temp_max_day1  \
0   WS_17047 2018-01-02     evening   heavy rain             10   
1   WS_17047 2018-01-02     morning   heavy rain             10   
2   WS_17062 2018-01-02     evening   heavy rain             12   
3   WS_17062 2018-01-02     morning   heavy rain             12   
4   WS_17063 2018-01-02     evening   heavy rain             13   

   temp_min_day1  humidity_max_day1  humidity_min_day1  wind_dir_day1  \
0              6               96.0               82.0            6.0   
1              6               96.0               82.0            6.0   
2              9               96.0               80.0           84.0   
3              9               96.0               80.0           84.0   
4              9               95.0               78.0           87.0   

   wind_speed_day1  ... humidity_min_day4  wind_dir_day4  wind_speed_day4  \
0             19.0  ...              57.0          185.0             12.0   
1             19.0  ...              57.0          185.0             12.0   
2             10.0  ...              57.0          114.0             10.0   
3             10.0  ...              57.0          114.0             10.0   
4             10.0  ...              57.0          134.0             11.0   

   weather_day5  temp_max_day5  temp_min_day5  humidity_max_day5  \
0    few clouds             14              8               90.0   
1    few clouds             14              8               90.0   
2    few clouds             17             10               78.0   
3    few clouds             17             10               78.0   
4    few clouds             17             10               78.0   

  humidity_min_day5  wind_dir_day5  wind_speed_day5  
0              70.0          210.0             16.0  
1              70.0          210.0             16.0  
2              67.0          107.0             14.0  
3              67.0          107.0             14.0  
4              63.0          131.0             14.0  

[5 rows x 38 columns]

In [9]:
#Read met-stations
met_stations = read_table_from_zip(data_zip_path, "met-stations.tsv")
print(f"met-stations.shape: {met_stations.shape}")
met_stations.head()

met-stations.shape: (20, 3)


station_no  height     clutter_class
0   WS_17047     381        DENSE TREE
1   WS_17062       5  LOW-MEDIUM URBAN
2   WS_17063      99           AIRPORT
3   WS_17064      18     OPEN IN URBAN
4   WS_17065     123  LOW-SPARSE URBAN

In [10]:
#Preapre Labels
# Firstly, only get unique entry identifiers and RLF column.
# For rl-kpis, unique entry identifiers are 'datetime', 'site_id' and 'mlid'.
df_labels = rl_kpis[["datetime", "site_id", "mlid"]]
df_labels.head()

datetime   site_id  mlid
0 2018-12-31  RL_;ABDV  A0BE
1 2018-12-31  RL_;ABDV  A0BI
2 2018-12-31  RL_;ABDV  A5AB
3 2018-12-31  RL_;ABDV  A8CQ
4 2018-12-31  RL_;ABDV  A8DQ

In [11]:
#Prepare target days (prediction days)

#  Prepare columns for the following days. We will join data with these columns to find RLF
prediction_interval = 5

for i in range(prediction_interval):
  df_labels[f"T+{i+1}"] = df_labels["datetime"] + pd.DateOffset(days=i+1)
df_labels.head()

C:\Users\gueyed\AppData\Local\Temp\1\ipykernel_13104\4001779457.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_labels[f"T+{i+1}"] = df_labels["datetime"] + pd.DateOffset(days=i+1)
C:\Users\gueyed\AppData\Local\Temp\1\ipykernel_13104\4001779457.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_labels[f"T+{i+1}"] = df_labels["datetime"] + pd.DateOffset(days=i+1)
C:\Users\gueyed\AppData\Local\Temp\1\ipykernel_13104\4001779457.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

datetime   site_id  mlid        T+1        T+2        T+3        T+4  \
0 2018-12-31  RL_;ABDV  A0BE 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
1 2018-12-31  RL_;ABDV  A0BI 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
2 2018-12-31  RL_;ABDV  A5AB 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
3 2018-12-31  RL_;ABDV  A8CQ 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
4 2018-12-31  RL_;ABDV  A8DQ 2019-01-01 2019-01-02 2019-01-03 2019-01-04   

         T+5  
0 2019-01-05  
1 2019-01-05  
2 2019-01-05  
3 2019-01-05  
4 2019-01-05

In [12]:
#Join dataset to get RLF colunms for the target days
rl_kpis_view = rl_kpis[["datetime", "site_id", "mlid", "rlf"]]
for i in range(prediction_interval):
  target_day_column_name = f"T+{i+1}"

  df_labels = df_labels.merge(rl_kpis_view, 
                  how = "left", 
                  left_on = ("site_id", "mlid", target_day_column_name),
                  right_on = ("site_id", "mlid", "datetime"),
                  suffixes = ("", "_y")
  )
  df_labels.rename(columns={"rlf": f"{target_day_column_name}_rlf"}, inplace=True)
df_labels.drop(columns=["datetime_y"], inplace=True)
df_labels.head()

datetime   site_id  mlid        T+1        T+2        T+3        T+4  \
0 2018-12-31  RL_;ABDV  A0BE 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
1 2018-12-31  RL_;ABDV  A0BI 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
2 2018-12-31  RL_;ABDV  A5AB 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
3 2018-12-31  RL_;ABDV  A8CQ 2019-01-01 2019-01-02 2019-01-03 2019-01-04   
4 2018-12-31  RL_;ABDV  A8DQ 2019-01-01 2019-01-02 2019-01-03 2019-01-04   

         T+5 T+1_rlf T+2_rlf T+3_rlf T+4_rlf T+5_rlf  
0 2019-01-05   False   False   False   False   False  
1 2019-01-05   False   False   False   False   False  
2 2019-01-05   False   False   False   False   False  
3 2019-01-05   False   False   False   False   False  
4 2019-01-05   False   False   False   False   False

In [13]:
#Finalize labels for 1-day and 5-day predictions
#For each link (site_id, mlid), we found the RLF for the 5-days (T+1.. T+5) following the given day (T). Now, we will finalize labelling

# 1 day predict is equal to T+1 rlf
df_labels["1-day-predict"] = df_labels["T+1_rlf"]

# Interval predict (5-day predict) is based on T+1, T+2, T+3, T+4 and T+5
following_days_rlf_columns = [f"T+{i+1}_rlf" for i in range(prediction_interval)]

df_labels["5-day-predict"] = df_labels[following_days_rlf_columns].any(axis=1)
df_labels = df_labels[["datetime", "site_id", "mlid", "1-day-predict", "5-day-predict"]]

print(f"df_labels.shape: {df_labels.shape}")
print(f"df_labels 1-day rlf sum: {df_labels['1-day-predict'].sum()}")
print(f"df_labels 5-day rlf sum: {df_labels['5-day-predict'].sum()}")
df_labels.head()

df_labels.shape: (1992986, 5)
df_labels 1-day rlf sum: 1204
df_labels 5-day rlf sum: 5159


datetime   site_id  mlid 1-day-predict  5-day-predict
0 2018-12-31  RL_;ABDV  A0BE         False          False
1 2018-12-31  RL_;ABDV  A0BI         False          False
2 2018-12-31  RL_;ABDV  A5AB         False          False
3 2018-12-31  RL_;ABDV  A8CQ         False          False
4 2018-12-31  RL_;ABDV  A8DQ         False          False

In [14]:
# Join labels with rl-kpis
rl_kpis_with_labels = rl_kpis.merge(df_labels, 
                                    how="left", 
                                    on=["datetime", "site_id", "mlid"])
rl_kpis_with_labels.head()

type   datetime  tip  mlid mw_connection_no   site_id  card_type  \
0  ENK 2018-12-31  FAR  A0BE        1,349,988  RL_;ABDV  cardtype1   
1  ENK 2018-12-31  FAR  A0BI        1,349,988  RL_;ABDV  cardtype1   
2  ENK 2018-12-31  FAR  A5AB        1,344,018  RL_;ABDV  cardtype4   
3  NEC 2018-12-31  FAR  A8CQ        1,351,204  RL_;ABDV  cardtype5   
4  NEC 2018-12-31  FAR  A8DQ        1,351,204  RL_;ABDV  cardtype5   

  adaptive_modulation freq_band  severaly_error_second  error_second  \
0              Enable        f3                    0.0           0.0   
1              Enable        f3                    0.0           0.0   
2              Enable        f3                    0.0           0.0   
3              Enable        f2                    0.0           0.0   
4              Enable        f2                    0.0           0.0   

   unavail_second  avail_time  bbe  rxlevmax  capacity modulation    rlf  \
0             0.0        86.4  0.0     -31.0     456.0    1024QAM  False   
1             0.0        86.4  0.0     -30.7     456.0    1024QAM  False   
2             0.0        86.4  0.0     -34.4     406.0     512QAM  False   
3             0.0        86.4  0.0     -35.3     247.0   2048QAM*  False   
4             0.0        86.4  0.0     -35.3     247.0   2048QAM*  False   

  1-day-predict  5-day-predict  
0         False          False  
1         False          False  
2         False          False  
3         False          False  
4         False          False

In [15]:
# Add rl-sites 
rl_kpis_with_sites = rl_kpis_with_labels.merge(rl_sites, on=["site_id"])
rl_kpis_with_sites.head()

type   datetime  tip  mlid mw_connection_no   site_id  card_type  \
0  ENK 2018-12-31  FAR  A0BE        1,349,988  RL_;ABDV  cardtype1   
1  ENK 2018-12-31  FAR  A0BI        1,349,988  RL_;ABDV  cardtype1   
2  ENK 2018-12-31  FAR  A5AB        1,344,018  RL_;ABDV  cardtype4   
3  NEC 2018-12-31  FAR  A8CQ        1,351,204  RL_;ABDV  cardtype5   
4  NEC 2018-12-31  FAR  A8DQ        1,351,204  RL_;ABDV  cardtype5   

  adaptive_modulation freq_band  severaly_error_second  ...  avail_time  bbe  \
0              Enable        f3                    0.0  ...        86.4  0.0   
1              Enable        f3                    0.0  ...        86.4  0.0   
2              Enable        f3                    0.0  ...        86.4  0.0   
3              Enable        f2                    0.0  ...        86.4  0.0   
4              Enable        f2                    0.0  ...        86.4  0.0   

   rxlevmax  capacity  modulation    rlf 1-day-predict  5-day-predict  \
0     -31.0     456.0     1024QAM  False         False          False   
1     -30.7     456.0     1024QAM  False         False          False   
2     -34.4     406.0      512QAM  False         False          False   
3     -35.3     247.0    2048QAM*  False         False          False   
4     -35.3     247.0    2048QAM*  False         False          False   

  groundheight  clutter_class  
0     107.9658      OPEN LAND  
1     107.9658      OPEN LAND  
2     107.9658      OPEN LAND  
3     107.9658      OPEN LAND  
4     107.9658      OPEN LAND  

[5 rows x 22 columns]

In [16]:
#Find closest station

#Step 1: Shaping the dataframe so that each row correspond to a weather station and each column corresponds to a rl
labels_station = met_stations["station_no"].values.tolist()
labels_rl_sites = rl_sites["site_id"].values.tolist()
distances.drop(columns=labels_station, inplace=True)
distances.drop(index=labels_rl_sites, inplace=True)
distances.head()


RL_U7MPL  RL_X;ORF  RL_X;OE?  RL_\K[RM  RL_UBUGK  RL_X;OQA  \
WS_19111  50.96124  63.36847  72.61144  68.53121  51.29432  59.53805   
WS_17047  67.19889  79.02323  87.01715  83.85289  67.36543  75.52589   
WS_18397  18.90229  15.90457  14.98860  16.23765  18.23613  17.07035   
WS_17062   9.65932  21.98328  32.30876  27.31256   9.90913  18.15286   
WS_17813   6.91141  19.15210  29.47758  24.48138   7.07795  15.32168   

          RL_\K[LJ  RL_L=SKK  RL_\K[QH  RL_\K[EJ  ...  RL_]=UC>  RL_]ITCK  \
WS_19111  70.86277  85.26848  65.94984  63.78482  ...  56.29052  39.88633   
WS_17047  86.35099  98.75822  82.10422  80.35555  ...  72.02855  55.54109   
WS_18397  18.73575  25.31408  20.31788  22.64944  ...  15.07187  22.73271   
WS_17062  29.56085  45.79850  24.64792  22.81598  ...  14.98860   3.49734   
WS_17813  26.72967  43.05059  21.81674  20.15134  ...  12.15742   5.24601   

          RL_[KBDF  RL_X;O@O  RL_b?LMI  RL_]IC?O  RL_S:PQD  RL_JEZWL  \
WS_19111  46.79774  59.53805  42.80078  41.30192  41.46846  47.79698   
WS_17047  63.03539  76.02551  58.87189  56.87341  57.53957  63.78482   
WS_18397  20.48442  20.40115  21.98328  21.65020  22.81598  18.98556   
WS_17062   5.49582  18.40267   1.66540   2.99772   0.91597   6.41179   
WS_17813   2.74791  15.73803   1.41559   3.99696   2.74791   3.58061   

          RL_LKEII  RL_[EOMJ  
WS_19111  52.29356  42.63424  
WS_17047  67.44870  58.62208  
WS_18397  12.82358  21.98328  
WS_17062  11.90761   1.49886  
WS_17813   9.24297   1.66540  

[5 rows x 1674 columns]

In [17]:
#Step2: Find clostest station
closest_station = distances.idxmin()
df_closest_station = closest_station.to_frame()
df_closest_station = df_closest_station.reset_index(level=0)
df_closest_station.set_axis(["site_id","station_no"], axis=1, inplace=True)
df_closest_station.head()

site_id station_no
0  RL_U7MPL   WS_17064
1  RL_X;ORF   WS_17063
2  RL_X;OE?   WS_18736
3  RL_\K[RM   WS_17063
4  RL_UBUGK   WS_17064

In [18]:
#Add weather stations information
rl_with_stations = rl_kpis_with_sites.merge(df_closest_station, on=["site_id"])
rl_with_stations.head()

type   datetime  tip  mlid mw_connection_no   site_id  card_type  \
0  ENK 2018-12-31  FAR  A0BE        1,349,988  RL_;ABDV  cardtype1   
1  ENK 2018-12-31  FAR  A0BI        1,349,988  RL_;ABDV  cardtype1   
2  ENK 2018-12-31  FAR  A5AB        1,344,018  RL_;ABDV  cardtype4   
3  NEC 2018-12-31  FAR  A8CQ        1,351,204  RL_;ABDV  cardtype5   
4  NEC 2018-12-31  FAR  A8DQ        1,351,204  RL_;ABDV  cardtype5   

  adaptive_modulation freq_band  severaly_error_second  ...  bbe  rxlevmax  \
0              Enable        f3                    0.0  ...  0.0     -31.0   
1              Enable        f3                    0.0  ...  0.0     -30.7   
2              Enable        f3                    0.0  ...  0.0     -34.4   
3              Enable        f2                    0.0  ...  0.0     -35.3   
4              Enable        f2                    0.0  ...  0.0     -35.3   

   capacity  modulation    rlf  1-day-predict 5-day-predict  groundheight  \
0     456.0     1024QAM  False          False         False      107.9658   
1     456.0     1024QAM  False          False         False      107.9658   
2     406.0      512QAM  False          False         False      107.9658   
3     247.0    2048QAM*  False          False         False      107.9658   
4     247.0    2048QAM*  False          False         False      107.9658   

  clutter_class  station_no  
0     OPEN LAND    WS_18403  
1     OPEN LAND    WS_18403  
2     OPEN LAND    WS_18403  
3     OPEN LAND    WS_18403  
4     OPEN LAND    WS_18403  

[5 rows x 23 columns]

In [19]:
#Add forecast
rl_final = rl_with_stations.merge(met_forecast.drop(index = [2*i for i in range(10161)]), how='outer', on=["station_no", "datetime"]) # We will consider only evening information

In [20]:
# Remove rows where the site-id is undefined
rl_final = rl_final.dropna(subset = ["site_id"])
print(rl_final.shape)
rl_final.head()

(1992986, 59)


type   datetime  tip  mlid mw_connection_no   site_id  card_type  \
0  ENK 2018-12-31  FAR  A0BE        1,349,988  RL_;ABDV  cardtype1   
1  ENK 2018-12-31  FAR  A0BI        1,349,988  RL_;ABDV  cardtype1   
2  ENK 2018-12-31  FAR  A5AB        1,344,018  RL_;ABDV  cardtype4   
3  NEC 2018-12-31  FAR  A8CQ        1,351,204  RL_;ABDV  cardtype5   
4  NEC 2018-12-31  FAR  A8DQ        1,351,204  RL_;ABDV  cardtype5   

  adaptive_modulation freq_band  severaly_error_second  ...  \
0              Enable        f3                    0.0  ...   
1              Enable        f3                    0.0  ...   
2              Enable        f3                    0.0  ...   
3              Enable        f2                    0.0  ...   
4              Enable        f2                    0.0  ...   

   humidity_min_day4  wind_dir_day4  wind_speed_day4  weather_day5  \
0                NaN            NaN              NaN           NaN   
1                NaN            NaN              NaN           NaN   
2                NaN            NaN              NaN           NaN   
3                NaN            NaN              NaN           NaN   
4                NaN            NaN              NaN           NaN   

   temp_max_day5  temp_min_day5 humidity_max_day5 humidity_min_day5  \
0            NaN            NaN               NaN               NaN   
1            NaN            NaN               NaN               NaN   
2            NaN            NaN               NaN               NaN   
3            NaN            NaN               NaN               NaN   
4            NaN            NaN               NaN               NaN   

  wind_dir_day5 wind_speed_day5  
0           NaN             NaN  
1           NaN             NaN  
2           NaN             NaN  
3           NaN             NaN  
4           NaN             NaN  

[5 rows x 59 columns]

## Model

### Preparing the data

In [21]:
# Features available
list(rl_final.columns)

['type',
 'datetime',
 'tip',
 'mlid',
 'mw_connection_no',
 'site_id',
 'card_type',
 'adaptive_modulation',
 'freq_band',
 'severaly_error_second',
 'error_second',
 'unavail_second',
 'avail_time',
 'bbe',
 'rxlevmax',
 'capacity',
 'modulation',
 'rlf',
 '1-day-predict',
 '5-day-predict',
 'groundheight',
 'clutter_class',
 'station_no',
 'report_time',
 'weather_day1',
 'temp_max_day1',
 'temp_min_day1',
 'humidity_max_day1',
 'humidity_min_day1',
 'wind_dir_day1',
 'wind_speed_day1',
 'weather_day2',
 'temp_max_day2',
 'temp_min_day2',
 'humidity_max_day2',
 'humidity_min_day2',
 'wind_dir_day2',
 'wind_speed_day2',
 'weather_day3',
 'temp_max_day3',
 'temp_min_day3',
 'humidity_max_day3',
 'humidity_min_day3',
 'wind_dir_day3',
 'wind_speed_day3',
 'weather_day4',
 'temp_max_day4',
 'temp_min_day4',
 'humidity_max_day4',
 'humidity_min_day4',
 'wind_dir_day4',
 'wind_speed_day4',
 'weather_day5',
 'temp_max_day5',
 'temp_min_day5',
 'humidity_max_day5',
 'humidity_min_day5',
 'w

In [22]:
#Feature Selection


categorical_features = ["card_type", "freq_band", "modulation", 'groundheight',
 'clutter_class','weather_day1','weather_day2','weather_day3','weather_day4','weather_day5', 'adaptive_modulation', ]
numerical_features = ["severaly_error_second", "error_second", "unavail_second", "bbe", "rxlevmax", "capacity", "avail_time", "temp_max_day1", "temp_max_day2",
                     "temp_max_day3", "temp_max_day4", "temp_max_day5",  "temp_min_day1", "temp_min_day2",
                     "temp_min_day3", "temp_min_day4", "temp_min_day5", "humidity_max_day1", "humidity_max_day2",
                     "humidity_max_day3", "humidity_max_day4", "humidity_max_day5",  "humidity_min_day1", "humidity_min_day2",
                     "humidity_min_day3", "humidity_min_day4", "humidity_min_day5", "wind_dir_day1", "wind_dir_day2", "wind_dir_day3", "wind_dir_day4", "wind_dir_day5", "wind_speed_day1", "wind_speed_day2", "wind_speed_day3", "wind_speed_day4", "wind_speed_day5"]

features = categorical_features + numerical_features

In [23]:
# Simple undersampling
np.random.seed(1234)

cond_rlf = rl_final["5-day-predict"].astype('bool') # otherwise some we have some -1
rlf_count = cond_rlf.sum()
print("rlf count: ", rlf_count)

# Get sample index from non rlf columns with 1:3 ratio
sampled_non_rlf_indicies = np.random.choice(rl_final[~cond_rlf].index, size=rlf_count*2)
rlf_indicies = np.array(rl_final[cond_rlf].index)

sampled_data_indicies = list(sampled_non_rlf_indicies) + list(rlf_indicies)
sampled_data = rl_final.loc[sampled_data_indicies]
sampled_data.shape

rlf count:  5159


(15477, 59)

In [24]:
#Splitting training and testing data (no CV so far)
df_training, df_test = train_test_split(sampled_data, test_size=0.2)
df_train, df_cv = train_test_split(df_training, test_size=0.25)
print(f"df_train.shape: {df_train.shape} | df_test.shape: {df_test.shape} | df_cv.shape: {df_cv.shape}")

df_train.shape: (9285, 59) | df_test.shape: (3096, 59) | df_cv.shape: (3096, 59)


In [25]:
# Convert categorical columns to one hot vector
# Merge them with numerical columns
# Return X data, column names, and encoder for future usage

def preprocessing(df, numerical_columns=[], categorical_columns=[], one_hot_encoder=None):

    # Handle NA
    # For this simple project, we just remove NA entities.
    df = df.dropna()

    if one_hot_encoder is None:
        print("Creating new one hot encoder")
        # For this project, handle one hot encoding here!
        one_hot_encoder = OneHotEncoder(handle_unknown="ignore", sparse=False)
        one_hot_encoder.fit(df[categorical_columns])
    
        print("one_hot_encoder: ", one_hot_encoder)
        print("*" * 50)
        print("Feature names: ", one_hot_encoder.get_feature_names())
        print("*" * 50)
        print("Categories: ", one_hot_encoder.categories_)

    arr_numerical = df[numerical_columns]
    arr_categorical = one_hot_encoder.transform(df[categorical_columns])
    feature_names = numerical_columns + list(one_hot_encoder.get_feature_names())
    arr_x = np.concatenate((arr_numerical, arr_categorical),axis=1)
    return df.copy(), arr_x, feature_names, one_hot_encoder

# Preprocess data, and get train data
df_train_dropped, train_x, feature_names, one_hot_encoder = preprocessing(df_train, 
                                                                         numerical_columns=numerical_features, 
                                                                         categorical_columns=categorical_features)

Creating new one hot encoder
one_hot_encoder:  OneHotEncoder(handle_unknown='ignore', sparse=False)
**************************************************
Feature names:  ['x0_cardtype1' 'x0_cardtype10' 'x0_cardtype11' 'x0_cardtype2'
 'x0_cardtype4' 'x0_cardtype5' 'x1_f1' 'x1_f2' 'x1_f3' 'x1_f4' 'x1_f5'
 'x2_1024 QAM' 'x2_1024QAM' 'x2_128QAM' 'x2_16QAM' 'x2_2048QAM'
 'x2_2048QAM*' 'x2_2048QAM_light*' 'x2_2048QAM_std*' 'x2_256QAM'
 'x2_256QAM(Q)' 'x2_512QAM' 'x2_512QAM(QO)' 'x2_64QAM' 'x3_1.0'
 'x3_1.0149' 'x3_2.0297' 'x3_3.0446' 'x3_3.9814' 'x3_4.9962' 'x3_6.0111'
 'x3_7.026' 'x3_8.0408' 'x3_8.9776' 'x3_9.9925' 'x3_11.0074' 'x3_12.0222'
 'x3_12.959' 'x3_13.9739' 'x3_14.9887' 'x3_16.0036' 'x3_17.0185'
 'x3_18.0333' 'x3_18.9701' 'x3_19.985' 'x3_20.9998' 'x3_22.0147'
 'x3_23.0296' 'x3_24.0444' 'x3_24.9812' 'x3_25.9961' 'x3_27.011'
 'x3_28.0258' 'x3_28.9626' 'x3_29.9775' 'x3_30.9923' 'x3_32.0072'
 'x3_32.944' 'x3_33.9589' 'x3_34.9737' 'x3_35.9886' 'x3_37.0034'
 'x3_38.0183' 'x3_39.0332' 'x3_39

C:\Program Files\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Program Files\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [26]:
train_x.shape

(6139, 386)

### XGBoost

In [27]:
# Buidling
clf_1_day = XGBClassifier(eta = 0.6)
clf_5_day = XGBClassifier(eta = 0.6)

In [28]:
# Training
train_y_1_day = df_train_dropped["1-day-predict"].astype('int').to_numpy()
train_y_5_day = df_train_dropped["5-day-predict"].astype('int').to_numpy()

clf_1_day.fit(train_x, train_y_1_day)
clf_5_day.fit(train_x, train_y_5_day)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False, eta=0.6,
              eval_metric=None, feature_types=None, gamma=0, gpu_id=-1,
              grow_policy='depthwise', importance_type=None,
              interaction_constraints='', learning_rate=0.600000024,
              max_bin=256, max_cat_threshold=64, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=0, num_parallel_tree=1, predictor='auto', ...)

In [85]:
feat_importances = pd.Series(clf_1_day.feature_importances_, index=feature_names)
plt.figure(figsize=(100, 100))
feat_importances.nlargest(50).plot(kind='barh', title = "Feature Importances for 1-Day Prediction", fontsize = 100) # 386 features in total

<AxesSubplot:title={'center':'Feature Importances for 1-Day Prediction'}>

In [52]:
feat_importances = pd.Series(clf_5_day.feature_importances_, index=feature_names)
plt.figure(figsize=(100, 100))
feat_importances.nlargest(50).plot(kind='barh', title = "Feature Importances for 5-Day Prediction", fontsize = 100) #386 features in total

<AxesSubplot:title={'center':'Feature Importances for 5-Day Prediction'}>

In [53]:
#Evaluating

# Preprocessing cv data
df_cv_dropepd, cv_x, _, _ = preprocessing(df_test, numerical_columns=numerical_features, 
                             categorical_columns=categorical_features, 
                             one_hot_encoder=one_hot_encoder)
cv_y_1_day = df_cv_dropepd["1-day-predict"].astype('int').to_numpy()
cv_y_5_day = df_cv_dropepd["5-day-predict"].astype('int').to_numpy()


# Preprocessing test data
df_test_dropepd, test_x, _, _ = preprocessing(df_test, numerical_columns=numerical_features, 
                             categorical_columns=categorical_features, 
                             one_hot_encoder=one_hot_encoder)
test_y_1_day = df_test_dropepd["1-day-predict"].astype('int').to_numpy()
test_y_5_day = df_test_dropepd["5-day-predict"].astype('int').to_numpy()

#Predicting
train_pred_1_day_xgboost = clf_1_day.predict(train_x)
cv_pred_1_day_xgboost = clf_1_day.predict(cv_x)
test_pred_1_day_xgboost = clf_1_day.predict(test_x)


train_pred_5_day_xgboost = clf_5_day.predict(train_x)
cv_pred_5_day_xgboost = clf_5_day.predict(cv_x)
test_pred_5_day_xgboost = clf_5_day.predict(test_x)

C:\Program Files\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Program Files\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [54]:
#pred 1 day

print("*********** SCORE for 1-DAY predict (Training Data) ***********")
print(classification_report(train_pred_1_day_xgboost,train_y_1_day))

print()
print("*********** SCORE for 1-DAY predict (CV Data) ***********")
print(classification_report(cv_pred_1_day_xgboost,cv_y_1_day))

*********** SCORE for 1-DAY predict (Training Data) ***********
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      5652
           1       1.00      1.00      1.00       487

    accuracy                           1.00      6139
   macro avg       1.00      1.00      1.00      6139
weighted avg       1.00      1.00      1.00      6139


*********** SCORE for 1-DAY predict (CV Data) ***********
              precision    recall  f1-score   support

           0       0.99      0.96      0.98      1931
           1       0.52      0.84      0.64       100

    accuracy                           0.95      2031
   macro avg       0.75      0.90      0.81      2031
weighted avg       0.97      0.95      0.96      2031



In [55]:
#pred 5 day

print("*********** SCORE for 5-DAY predict (Training Data) ***********")
print(classification_report(train_pred_5_day_xgboost,train_y_5_day))

print()
print("*********** SCORE for 5-DAY predict (CV Data) ***********")
print(classification_report(cv_pred_5_day_xgboost,cv_y_5_day))


*********** SCORE for 5-DAY predict (Training Data) ***********
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      4067
           1       1.00      1.00      1.00      2072

    accuracy                           1.00      6139
   macro avg       1.00      1.00      1.00      6139
weighted avg       1.00      1.00      1.00      6139


*********** SCORE for 5-DAY predict (CV Data) ***********
              precision    recall  f1-score   support

           0       0.92      0.90      0.91      1373
           1       0.80      0.83      0.82       658

    accuracy                           0.88      2031
   macro avg       0.86      0.87      0.86      2031
weighted avg       0.88      0.88      0.88      2031



In [56]:
#Testing

print("*********** SCORE for 1-DAY predict (Testing Data) ***********")
print(classification_report(test_pred_1_day_xgboost,test_y_1_day))

print()
print("*********** SCORE for 5-DAY predict (Testing Data) ***********")
print(classification_report(test_pred_5_day_xgboost,test_y_5_day))

*********** SCORE for 1-DAY predict (Testing Data) ***********
              precision    recall  f1-score   support

           0       0.99      0.96      0.98      1931
           1       0.52      0.84      0.64       100

    accuracy                           0.95      2031
   macro avg       0.75      0.90      0.81      2031
weighted avg       0.97      0.95      0.96      2031


*********** SCORE for 5-DAY predict (Testing Data) ***********
              precision    recall  f1-score   support

           0       0.92      0.90      0.91      1373
           1       0.80      0.83      0.82       658

    accuracy                           0.88      2031
   macro avg       0.86      0.87      0.86      2031
weighted avg       0.88      0.88      0.88      2031



### LSTM

In [57]:
# Building the model

print(train_x.shape)
train_x_dim = np.reshape(train_x,(train_x.shape[0],1, train_x.shape[1]))
print(train_x_dim.shape)

model_1_day = Sequential(
    [                
        #tf.keras.Input(shape=train_x.shape),  
        layers.LSTM(100, input_shape = (1,386), name = 'layer1'),
        layers.Dense(25, activation = 'sigmoid', name = 'layer2'),
        layers.Dense(2, activation = 'linear', name = 'layer3')

    ], name = "LSTMmodelDay1" 
)

print(model_1_day.summary())

(6139, 386)
(6139, 1, 386)
Model: "LSTMmodelDay1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 layer1 (LSTM)               (None, 100)               194800    
                                                                 
 layer2 (Dense)              (None, 25)                2525      
                                                                 
 layer3 (Dense)              (None, 2)                 52        
                                                                 
Total params: 197,377
Trainable params: 197,377
Non-trainable params: 0
_________________________________________________________________
None


In [58]:
# Building the model

model_5_day = Sequential(
    [                
        #tf.keras.Input(shape=train_x.shape),  
        layers.LSTM(100, input_shape = (1,386), name = 'layer1'),
        layers.Dense(25, activation = 'sigmoid', name = 'layer2'),
        layers.Dense(2, activation = 'linear', name = 'layer3')

    ], name = "LSTMmodelDay5" 
)

print(model_5_day.summary())

Model: "LSTMmodelDay5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 layer1 (LSTM)               (None, 100)               194800    
                                                                 
 layer2 (Dense)              (None, 25)                2525      
                                                                 
 layer3 (Dense)              (None, 2)                 52        
                                                                 
Total params: 197,377
Trainable params: 197,377
Non-trainable params: 0
_________________________________________________________________
None


In [59]:
# Training 

model_1_day.compile(
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),
    metrics=[keras.metrics.SparseCategoricalAccuracy()]
)

history = model_1_day.fit(
    train_x_dim, train_y_1_day,
    epochs=40
)

Epoch 1/40
192/192 [==============================] - 6s 10ms/step - loss: 0.2702 - sparse_categorical_accuracy: 0.9207
Epoch 2/40
192/192 [==============================] - 1s 6ms/step - loss: 0.2584 - sparse_categorical_accuracy: 0.9207
Epoch 3/40
192/192 [==============================] - 1s 6ms/step - loss: 0.2556 - sparse_categorical_accuracy: 0.9207
Epoch 4/40
192/192 [==============================] - 1s 5ms/step - loss: 0.2507 - sparse_categorical_accuracy: 0.9205
Epoch 5/40
192/192 [==============================] - 1s 6ms/step - loss: 0.2472 - sparse_categorical_accuracy: 0.9203
Epoch 6/40
192/192 [==============================] - 1s 5ms/step - loss: 0.2436 - sparse_categorical_accuracy: 0.9207
Epoch 7/40
192/192 [==============================] - 1s 5ms/step - loss: 0.2364 - sparse_categorical_accuracy: 0.9213
Epoch 8/40
192/192 [==============================] - 1s 6ms/step - loss: 0.2319 - sparse_categorical_accuracy: 0.9213
Epoch 9/40
192/192 [===========================

In [60]:
# Training 

model_5_day.compile(
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),
    metrics=[keras.metrics.SparseCategoricalAccuracy()]
)

history = model_5_day.fit(
    train_x_dim, train_y_5_day,
    epochs=40
)

Epoch 1/40
192/192 [==============================] - 3s 6ms/step - loss: 0.6031 - sparse_categorical_accuracy: 0.6739
Epoch 2/40
192/192 [==============================] - 1s 5ms/step - loss: 0.5827 - sparse_categorical_accuracy: 0.6931
Epoch 3/40
192/192 [==============================] - 1s 4ms/step - loss: 0.5725 - sparse_categorical_accuracy: 0.6956
Epoch 4/40
192/192 [==============================] - 1s 4ms/step - loss: 0.5626 - sparse_categorical_accuracy: 0.7099
Epoch 5/40
192/192 [==============================] - 1s 5ms/step - loss: 0.5538 - sparse_categorical_accuracy: 0.7161
Epoch 6/40
192/192 [==============================] - 1s 4ms/step - loss: 0.5446 - sparse_categorical_accuracy: 0.7263
Epoch 7/40
192/192 [==============================] - 1s 5ms/step - loss: 0.5363 - sparse_categorical_accuracy: 0.7302
Epoch 8/40
192/192 [==============================] - 1s 4ms/step - loss: 0.5400 - sparse_categorical_accuracy: 0.7263
Epoch 9/40
192/192 [============================

In [61]:
#Evaluating

#Reshaping
cv_x_dim = np.reshape(cv_x,(cv_x.shape[0],1, train_x.shape[1]))
test_x_dim = np.reshape(test_x,(test_x.shape[0],1, test_x.shape[1]))

#Predicting 

train_pred_1_day_lstm = [np.argmax(i) for i in model_1_day.predict(train_x_dim)]
cv_pred_1_day_lstm = [np.argmax(i) for i in model_1_day.predict(cv_x_dim)]
test_pred_1_day_lstm = [np.argmax(i) for i in model_1_day.predict(test_x_dim)]

train_pred_5_day_lstm = [np.argmax(i) for i in model_5_day.predict(train_x_dim)]
cv_pred_5_day_lstm = [np.argmax(i) for i in model_5_day.predict(cv_x_dim)]
test_pred_5_day_lstm = [np.argmax(i) for i in model_5_day.predict(test_x_dim)]

64/64 [==============================] - 0s 3ms/step


In [62]:
#pred 1 day

print("*********** SCORE for 1-DAY predict (Training Data) ***********")
print(classification_report(train_pred_1_day_lstm,train_y_1_day))


print()
print("*********** SCORE for 1-DAY predict (CV Data) ***********")
print(classification_report(cv_pred_1_day_lstm,cv_y_1_day))

*********** SCORE for 1-DAY predict (Training Data) ***********
              precision    recall  f1-score   support

           0       0.98      0.95      0.97      5803
           1       0.46      0.66      0.54       336

    accuracy                           0.94      6139
   macro avg       0.72      0.81      0.75      6139
weighted avg       0.95      0.94      0.94      6139


*********** SCORE for 1-DAY predict (CV Data) ***********
              precision    recall  f1-score   support

           0       0.98      0.94      0.96      1945
           1       0.34      0.64      0.44        86

    accuracy                           0.93      2031
   macro avg       0.66      0.79      0.70      2031
weighted avg       0.96      0.93      0.94      2031



In [63]:
#pred 5 day

print("*********** SCORE for 5-DAY predict (Training Data)***********")
print(classification_report(train_pred_5_day_lstm,train_y_5_day))


print()
print("*********** SCORE for 5-DAY predict (CV Data) ***********")
print(classification_report(cv_pred_5_day_lstm,cv_y_5_day))

*********** SCORE for 5-DAY predict (Training Data)***********
              precision    recall  f1-score   support

           0       0.77      0.88      0.82      3567
           1       0.79      0.64      0.71      2572

    accuracy                           0.78      6139
   macro avg       0.78      0.76      0.76      6139
weighted avg       0.78      0.78      0.77      6139


*********** SCORE for 5-DAY predict (CV Data) ***********
              precision    recall  f1-score   support

           0       0.77      0.87      0.82      1201
           1       0.77      0.63      0.69       830

    accuracy                           0.77      2031
   macro avg       0.77      0.75      0.76      2031
weighted avg       0.77      0.77      0.77      2031



In [64]:
#Testing

print("*********** SCORE for 1-DAY predict (Testing Data) ***********")
print(classification_report(test_pred_1_day_lstm,test_y_1_day))


print()
print("*********** SCORE for 5-DAY predict (Testing Data) ***********")
print(classification_report(test_pred_5_day_lstm,test_y_5_day))

*********** SCORE for 1-DAY predict (Testing Data) ***********
              precision    recall  f1-score   support

           0       0.98      0.94      0.96      1945
           1       0.34      0.64      0.44        86

    accuracy                           0.93      2031
   macro avg       0.66      0.79      0.70      2031
weighted avg       0.96      0.93      0.94      2031


*********** SCORE for 5-DAY predict (Testing Data) ***********
              precision    recall  f1-score   support

           0       0.77      0.87      0.82      1201
           1       0.77      0.63      0.69       830

    accuracy                           0.77      2031
   macro avg       0.77      0.75      0.76      2031
weighted avg       0.77      0.77      0.77      2031



### Neural Network

In [65]:
# Building the model

print(train_x.shape)

model_1_day_dense = Sequential(
    [                
        tf.keras.Input(shape=(386,)),
        layers.Dense(100, activation = 'sigmoid', name = 'layer1'),
        layers.Dense(2, activation = 'linear', name = 'layer2')

    ], name = "ModelDay1" 
)

print(model_1_day_dense.summary())

(6139, 386)
Model: "ModelDay1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 layer1 (Dense)              (None, 100)               38700     
                                                                 
 layer2 (Dense)              (None, 2)                 202       
                                                                 
Total params: 38,902
Trainable params: 38,902
Non-trainable params: 0
_________________________________________________________________
None


In [66]:
# Building the model

model_5_day_dense = Sequential(
    [                
        tf.keras.Input(shape=(386,)),  
        layers.Dense(100, activation = 'sigmoid', name = 'layer1'),
        layers.Dense(2, activation = 'linear', name = 'layer2')

    ], name = "ModelDay5" 
)

print(model_5_day_dense.summary())

Model: "ModelDay5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 layer1 (Dense)              (None, 100)               38700     
                                                                 
 layer2 (Dense)              (None, 2)                 202       
                                                                 
Total params: 38,902
Trainable params: 38,902
Non-trainable params: 0
_________________________________________________________________
None


In [67]:
# Training 

model_1_day_dense.compile(
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),
    metrics=[keras.metrics.SparseCategoricalAccuracy()]
)

history = model_1_day_dense.fit(
    train_x, train_y_1_day,
    epochs=40
)

Epoch 1/40
192/192 [==============================] - 1s 2ms/step - loss: 0.2720 - sparse_categorical_accuracy: 0.9182
Epoch 2/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2504 - sparse_categorical_accuracy: 0.9205
Epoch 3/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2459 - sparse_categorical_accuracy: 0.9215
Epoch 4/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2429 - sparse_categorical_accuracy: 0.9208
Epoch 5/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2371 - sparse_categorical_accuracy: 0.9210
Epoch 6/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2313 - sparse_categorical_accuracy: 0.9216
Epoch 7/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2320 - sparse_categorical_accuracy: 0.9215
Epoch 8/40
192/192 [==============================] - 0s 2ms/step - loss: 0.2256 - sparse_categorical_accuracy: 0.9220
Epoch 9/40
192/192 [============================

In [68]:
# Training 

model_5_day_dense.compile(
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),
    metrics=[keras.metrics.SparseCategoricalAccuracy()]
)

history = model_5_day_dense.fit(
    train_x, train_y_5_day,
    epochs=40
)

Epoch 1/40
192/192 [==============================] - 1s 2ms/step - loss: 0.6036 - sparse_categorical_accuracy: 0.6721
Epoch 2/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5690 - sparse_categorical_accuracy: 0.7066
Epoch 3/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5584 - sparse_categorical_accuracy: 0.7127
Epoch 4/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5506 - sparse_categorical_accuracy: 0.7213
Epoch 5/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5430 - sparse_categorical_accuracy: 0.7245
Epoch 6/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5391 - sparse_categorical_accuracy: 0.7348
Epoch 7/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5305 - sparse_categorical_accuracy: 0.7408
Epoch 8/40
192/192 [==============================] - 0s 2ms/step - loss: 0.5231 - sparse_categorical_accuracy: 0.7439
Epoch 9/40
192/192 [============================

In [69]:
#Evaluating

#Predicting 

train_pred_1_day_dense= [np.argmax(i) for i in model_1_day_dense.predict(train_x)]
cv_pred_1_day_dense = [np.argmax(i) for i in model_1_day_dense.predict(cv_x)]
test_pred_1_day_dense = [np.argmax(i) for i in model_1_day_dense.predict(test_x)]

train_pred_5_day_dense = [np.argmax(i) for i in model_5_day_dense.predict(train_x)]
cv_pred_5_day_dense = [np.argmax(i) for i in model_5_day_dense.predict(cv_x)]
test_pred_5_day_dense = [np.argmax(i) for i in model_5_day_dense.predict(test_x)]

64/64 [==============================] - 0s 1ms/step


In [70]:
#pred 1 day

print("*********** SCORE for 1-DAY predict (Training Data) ***********")
print(classification_report(train_pred_1_day_dense,train_y_1_day))


print()
print("*********** SCORE for 1-DAY predict (CV Data) ***********")
print(classification_report(cv_pred_1_day_dense,cv_y_1_day))

*********** SCORE for 1-DAY predict (Training Data) ***********
              precision    recall  f1-score   support

           0       0.98      0.95      0.96      5833
           1       0.38      0.61      0.47       306

    accuracy                           0.93      6139
   macro avg       0.68      0.78      0.72      6139
weighted avg       0.95      0.93      0.94      6139


*********** SCORE for 1-DAY predict (CV Data) ***********
              precision    recall  f1-score   support

           0       0.97      0.95      0.96      1912
           1       0.37      0.50      0.43       119

    accuracy                           0.92      2031
   macro avg       0.67      0.73      0.69      2031
weighted avg       0.93      0.92      0.93      2031



In [71]:
#pred 5 day

print("*********** SCORE for 5-DAY predict (Training Data) ***********")
print(classification_report(train_pred_5_day_dense,train_y_5_day))

print()
print("*********** SCORE for 5-DAY predict (CV Data) ***********")
print(classification_report(cv_pred_5_day_dense,cv_y_5_day))

*********** SCORE for 5-DAY predict (Training Data) ***********
              precision    recall  f1-score   support

           0       0.96      0.78      0.86      4981
           1       0.47      0.85      0.61      1158

    accuracy                           0.79      6139
   macro avg       0.72      0.82      0.73      6139
weighted avg       0.87      0.79      0.81      6139


*********** SCORE for 5-DAY predict (CV Data) ***********
              precision    recall  f1-score   support

           0       0.94      0.76      0.84      1671
           1       0.42      0.79      0.55       360

    accuracy                           0.77      2031
   macro avg       0.68      0.78      0.70      2031
weighted avg       0.85      0.77      0.79      2031



In [72]:
#Testing

print()
print("*********** SCORE for 1-DAY predict (Testing Data) ***********")
print(classification_report(test_pred_1_day_dense,test_y_1_day))


print()
print("*********** SCORE for 5-DAY predict (Testing Data) ***********")
print(classification_report(test_pred_5_day_dense,test_y_5_day))


*********** SCORE for 1-DAY predict (Testing Data) ***********
              precision    recall  f1-score   support

           0       0.97      0.95      0.96      1912
           1       0.37      0.50      0.43       119

    accuracy                           0.92      2031
   macro avg       0.67      0.73      0.69      2031
weighted avg       0.93      0.92      0.93      2031


*********** SCORE for 5-DAY predict (Testing Data) ***********
              precision    recall  f1-score   support

           0       0.94      0.76      0.84      1671
           1       0.42      0.79      0.55       360

    accuracy                           0.77      2031
   macro avg       0.68      0.78      0.70      2031
weighted avg       0.85      0.77      0.79      2031

